In [1]:
import tensorflow as tf
import tensorlayer as tl
import numpy as np
import sys
import os
import math
from tensorflow.python.keras.initializers import he_normal
import random
import cv2
from tensorflow.python.framework.graph_util import convert_variables_to_constants

/opt/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
tf.app.flags.DEFINE_integer('image_size', 416, "Needs to provide same value as in training.")
tf.app.flags.DEFINE_string('checkpoint_dir', './checkpoint', 'the checkpoint dir')
tf.app.flags.DEFINE_string('log_dir', './log', 'the logging dir')
tf.app.flags.DEFINE_integer('batch_size', 16, 'Validation batch size')
tf.app.flags.DEFINE_integer('num_classes', 37,'The num of classes need to predict')
FLAGS = tf.app.flags.FLAGS
tf.app.flags.DEFINE_string('f', '', 'kernel')

In [3]:
def convolutional_block(layer,layer_depth,is_training):
    depth1,depth2,depth3 = layer_depth
    shortcut = layer
    conv_layer1 = tf.layers.conv2d(layer, depth1, [1,1], 2, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    conv_layer1_bn = tf.layers.batch_normalization(conv_layer1, training=is_training)
    conv_layer1_out = tf.nn.relu(conv_layer1_bn)
    
    conv_layer2 = tf.layers.conv2d(conv_layer1_out, depth2, [3,3], 1, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    conv_layer2_bn = tf.layers.batch_normalization(conv_layer2, training=is_training)
    conv_layer2_out = tf.nn.relu(conv_layer2_bn)
    
    conv_layer3 = tf.layers.conv2d(conv_layer2_out, depth3, [1,1], 1, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    conv_layer3_bn = tf.layers.batch_normalization(conv_layer3, training=is_training)
    
    conv_temp = tf.layers.conv2d(shortcut,depth3,[1,1],2,'same')
    conv_temp = tf.layers.batch_normalization(conv_temp,training=is_training)
    conv_add = conv_temp+conv_layer3_bn
    conv_layer3_out = tf.nn.relu(conv_add)
#     pool_layer3 = tf.layers.max_pooling2d(conv_layer3_out,[2,2],strides=2)
    return conv_layer3_out

In [4]:
def identity_block(layer,layer_depth,is_training):
    depth1,depth2,depth3 = layer_depth
    shortcut = layer
    conv_layer1 = tf.layers.conv2d(layer, depth1, [1,1], 1, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    conv_layer1_bn = tf.layers.batch_normalization(conv_layer1, training=is_training)
    conv_layer1_out = tf.nn.relu(conv_layer1_bn)
    
    conv_layer2 = tf.layers.conv2d(conv_layer1_out, depth2, [3,3], 1, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    conv_layer2_bn = tf.layers.batch_normalization(conv_layer2, training=is_training)
    conv_layer2_out = tf.nn.relu(conv_layer2_bn)
    
    conv_layer3 = tf.layers.conv2d(conv_layer2_out, depth3, [1,1], 1, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    conv_layer3_bn = tf.layers.batch_normalization(conv_layer3, training=is_training)
    
#     conv_temp = tf.layers.conv2d(shortcut,depth3,[1,1],1,'same')
    conv_add = shortcut+conv_layer3_bn
    conv_layer3_out = tf.nn.relu(conv_add)

    return conv_layer3_out

In [5]:
def preprocess_true_boxes(true_boxes, input_shape, anchors, num_classes):
    '''Preprocess true boxes to training input format

    Parameters
    ----------
    true_boxes: array, shape=(m, T, 5)
        Absolute x_min, y_min, x_max, y_max, class_id relative to input_shape.
    input_shape: array-like, hw, multiples of 32
    anchors: array, shape=(N, 2), wh
    num_classes: integer

    Returns
    -------
    y_true: list of array, shape like yolo_outputs, xywh are reletive value

    '''
#     assert (true_boxes[..., 4]<num_classes).all(), 'class id must be less than num_classes'
    num_layers = len(anchors)//3 # tiny yolo only 2 feat layers
    anchor_mask = [[6,7,8], [3,4,5], [0,1,2]] if num_layers==3 else [[3,4,5], [1,2,3]]
#     print(anchor_mask)
    true_boxes = np.array(true_boxes, dtype='float32')
    input_shape = np.array(input_shape, dtype='int32')
    boxes_xy = (true_boxes[..., 0:2] + true_boxes[..., 2:4]) // 2
    boxes_wh = true_boxes[..., 2:4] - true_boxes[..., 0:2]
    true_boxes[..., 0:2] = boxes_xy/input_shape[::-1]
    true_boxes[..., 2:4] = boxes_wh/input_shape[::-1]

    m = true_boxes.shape[0]#batch_size
    grid_shapes = [input_shape//{0:32, 1:16, 2:8}[l] for l in range(num_layers)]
    y_true = [np.zeros((m,grid_shapes[l][0],grid_shapes[l][1],len(anchor_mask[l]),5+num_classes),
        dtype='float32') for l in range(num_layers)]

    # Expand dim to apply broadcasting.
    anchors = np.expand_dims(anchors, 0)
    anchor_maxes = anchors / 2.
    anchor_mins = -anchor_maxes
    valid_mask = boxes_wh[..., 0]>0

    for b in range(m):
        # Discard zero rows.
        wh = boxes_wh[b, valid_mask[b]] ##(batch,num_valid_boxes,2)
        if len(wh)==0: continue
        # Expand dim to apply broadcasting.
        wh = np.expand_dims(wh, -2)#(batch,num_valid_boxes,1,2)
        box_maxes = wh / 2.
        box_mins = -box_maxes

        intersect_mins = np.maximum(box_mins, anchor_mins) #(batch,num_valid_boxes,9,2)
        intersect_maxes = np.minimum(box_maxes, anchor_maxes)
        intersect_wh = np.maximum(intersect_maxes - intersect_mins, 0.)
        intersect_area = intersect_wh[..., 0] * intersect_wh[..., 1]
        box_area = wh[..., 0] * wh[..., 1]
        anchor_area = anchors[..., 0] * anchors[..., 1]
        iou = intersect_area / (box_area + anchor_area - intersect_area)
        # Find best anchor for each true box
        best_anchor = np.argmax(iou, axis=-1)

        count = 0
        for t, n in enumerate(best_anchor):
            for l in range(num_layers):
                if n in anchor_mask[l]:
                    i = np.floor(true_boxes[b,t,0]*grid_shapes[l][1]).astype('int32')
                    j = np.floor(true_boxes[b,t,1]*grid_shapes[l][0]).astype('int32')
                    k = anchor_mask[l].index(n)
                    c = true_boxes[b,t, 4].astype('int32')
                    y_true[l][b, j, i, k, 0:4] = true_boxes[b,t, 0:4]
                    y_true[l][b, j, i, k, 4] = 1
                    y_true[l][b, j, i, k, 5+c] = 1
#                     print([l,b,j,i,k,5+c])
#[batch_size,layers,feat_size,feat_size,num_of_anchors each layer,c+5]
    return y_true


def box_iou(b1, b2):
    '''Return iou tensor

    Parameters
    ----------
    b1: tensor, shape=(i1,...,iN, 4), xywh
    b2: tensor, shape=(j, 4), xywh

    Returns
    -------
    iou: tensor, shape=(i1,...,iN, j)

    '''

    # Expand dim to apply broadcasting.
    b1 = tf.expand_dims(b1, -2)
    b1_xy = b1[..., :2]
    b1_wh = b1[..., 2:4]
    b1_wh_half = b1_wh/2.
    b1_mins = b1_xy - b1_wh_half
    b1_maxes = b1_xy + b1_wh_half

    # Expand dim to apply broadcasting.
    b2 = tf.expand_dims(b2, 0)
    b2_xy = b2[..., :2]
    b2_wh = b2[..., 2:4]
    b2_wh_half = b2_wh/2.
    b2_mins = b2_xy - b2_wh_half
    b2_maxes = b2_xy + b2_wh_half

    intersect_mins = tf.maximum(b1_mins, b2_mins)
    intersect_maxes = tf.minimum(b1_maxes, b2_maxes)
    intersect_wh = tf.maximum(intersect_maxes - intersect_mins, 0.)
    intersect_area = intersect_wh[..., 0] * intersect_wh[..., 1]
    b1_area = b1_wh[..., 0] * b1_wh[..., 1]
    b2_area = b2_wh[..., 0] * b2_wh[..., 1]
    iou = intersect_area / (b1_area + b2_area - intersect_area)

    return iou

In [6]:
def identity_block_2(layer,layer_depth,is_training):
    depth1,depth2 = layer_depth
    shortcut = layer
    conv_layer1 = tf.layers.conv2d(layer, depth1, [1,1], 1, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    conv_layer1_bn = tf.layers.batch_normalization(conv_layer1, training=is_training)
    conv_layer1_out = tf.nn.relu(conv_layer1_bn)
    
    conv_layer2 = tf.layers.conv2d(conv_layer1_out, depth2, [3,3], 1, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    conv_layer2_bn = tf.layers.batch_normalization(conv_layer2, training=is_training)

    conv_add = shortcut+conv_layer2_bn
    conv_layer2_out = tf.nn.leaky_relu(conv_add,alpha=0.1)

    return conv_layer2_out

In [7]:
def conv2d_bn_leak(layer,depth,stride,kernel_size,is_training):
    if stride ==1:
        padding ='same'
    else:
        padding ='valid'
    X = tf.layers.conv2d(inputs=layer,filters=depth,kernel_size=kernel_size,strides=stride,padding=padding,use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(5e-4))
    X = tf.layers.batch_normalization(X,training=is_training)
    X = tf.nn.leaky_relu(X,alpha=0.1)
    return X

In [8]:
def bottle_neck(layer,is_training):
    #------------bottleneck for yolo(darknet53)-----------
    X = conv2d_bn_leak(layer,32,1,[3,3],is_training)
    X = tf.pad(X,[[0,0],[1,0],[1,0],[0,0]])
    X = conv2d_bn_leak(X,64,2,[3,3],is_training)
    #------------
    X = identity_block_2(X,[32,64],is_training)
    #-------------
    X = tf.pad(X,[[0,0],[1,0],[1,0],[0,0]])
    X = conv2d_bn_leak(X,128,2,[3,3],is_training)
    #-------------res*2
    X = identity_block_2(X,[64,128],is_training)
    X = identity_block_2(X,[64,128],is_training)
    #-------------
    X = tf.pad(X,[[0,0],[1,0],[1,0],[0,0]])
    X = conv2d_bn_leak(X,256,2,[3,3],is_training)
    #-------------resnet*8
    for i in range(8):
        X = identity_block_2(X,[128,256],is_training)
    scale3 = X
    #-------------conv
    X = tf.pad(X,[[0,0],[1,0],[1,0],[0,0]])
    X = conv2d_bn_leak(X,512,2,[3,3],is_training)
    #-------------resnet*8
    for i in range(8):
        X = identity_block_2(X,[256,512],is_training) 
    scale2 = X
    #------------conv
    X = tf.pad(X,[[0,0],[1,0],[1,0],[0,0]])
    X = conv2d_bn_leak(X,1024,2,[3,3],is_training)
    #-----------resnet*4
    for i in range(4):
        X = identity_block_2(X,[512,1024],is_training) 
    #-----------avg-pooling
#     X = tf.layers.average_pooling2d(X,[2,2],strides=1)
    scale1 = X
    return X,scale1,scale2,scale3

In [9]:
def scale(X,scale,depth,num_anchors,num_class,is_training):
    if(depth!=512):
        X = conv2d_bn_leak(X,depth,1,[3,3],is_training)
        X = tf.image.resize_nearest_neighbor(X,(X.shape[1]*2,X.shape[2]*2))
#         print(scale2.shape)
#         print(X.shape)
        X = tf.concat([X,scale],axis=3)

    #scale1 13*13
    X = conv2d_bn_leak(X,depth,1,[1,1],is_training)
    X = conv2d_bn_leak(X,depth*2,1,[3,3],is_training)
    X = conv2d_bn_leak(X,depth,1,[1,1],is_training)
    X = conv2d_bn_leak(X,depth*2,1,[3,3],is_training)
    X = conv2d_bn_leak(X,depth,1,[1,1],is_training)

    scale = conv2d_bn_leak(scale,depth*2,1,[3,3],is_training)
    scale = tf.layers.conv2d(scale, num_anchors*(num_class+5), [1,1], 1, 'same', use_bias=True,kernel_initializer=he_normal(seed=0.01),activation=None,kernel_regularizer=tf.contrib.layers.l2_regularizer(0.01))
    return X,scale

In [10]:
# img_path, annotation = get_path_and_annotation('./data/train_ocr.txt')
# train_feeder = read_data(img_path,annotation,FLAGS.batch_size,False)
# image_batch, annotation_batch = next(train_feeder)

In [11]:
# annotation_batch[0][...,0:4]

In [12]:
def data_augmentation(img,annotation):
    for anno in annotation:
        coords = []
        xywh_t = []
        for i in anno[...,0:4]:
            coords.append(tl.prepro.obj_box_coord_upleft_butright_to_centroid(i))
        im_flip, coords = tl.prepro.obj_box_left_right_flip(img,coords,is_rescale=False,is_center=True)
        for i in range(len(coords)):
            xywh_t.append(tl.prepro.obj_box_coord_centroid_to_upleft_butright(coords[i]))
    return xywh_t
    

In [13]:
def read_data(img_list,annotation,batch_size,aug):
    num_batch = len(img_list)/batch_size
    count=0
    while(True):
        image_data = []
        annotation_data = []
        for i in range(batch_size):
            temp_index = i+count*batch_size
            temp_index %=len(img_list) 
            image = cv2.imread(img_list[temp_index])
            if aug:
                image = data_augmentation(image)
            image = image[:,:,::-1]
            image = image.astype(np.float32)
            image_shape = image.shape
#             image = cv2.resize(image,(FLAGS.image_size,FLAGS.image_size))
            
#             image = image/255
            image_data.append(image)
            annotation_data.append(np.array(annotation[temp_index]).astype(np.int32))
        count+=1
        image_data = np.array(image_data)
        yield image_data,annotation_data

def get_path_and_annotation(file_path):
    annotation = []
    img_path = []
    line_list = []
    with open(file_path,'r') as f:
        for line in f:
            temp=[]
            line = line.strip('\n')
            line_list.append(line)
        random.shuffle(line_list)

    for i in line_list:
        line = i.split(' ')
        img_path.append(line[0])
        temp = []
        temp_inner= []
        for j in range(1,len(line)):
            temp.append(line[j].split(','))
        annotation.append(temp)
    return img_path,annotation


def resize_images_boxes(image_batch,annotation_batch,max_num_box):
    batch_size = image_batch.shape[0]
    bbox = np.zeros((batch_size,max_num_box,5))
#     target_size = FLAGS.image_size
    image_size = (image_batch.shape[1],image_batch.shape[2])
    x_ratio = FLAGS.image_size/image_size[1]
    y_ratio = FLAGS.image_size/image_size[0]
    temp_image = []
    for i in range(batch_size):
        temp_image.append(cv2.resize(image_batch[i],(FLAGS.image_size,FLAGS.image_size)))
        for j in range(len(annotation_batch[i])):
            bbox[i][j][0]= np.round(annotation_batch[i][j][0]*x_ratio)
            bbox[i][j][1]= np.round(annotation_batch[i][j][1]*y_ratio)
            bbox[i][j][2]= np.round(annotation_batch[i][j][2]*x_ratio)
            bbox[i][j][3]= np.round(annotation_batch[i][j][3]*y_ratio)
            bbox[i][j][4]= annotation_batch[i][j][4]
    return np.array(temp_image,dtype=np.float32),bbox

In [14]:
def yolo3_loss(y_pred, y_true,anchors):
    anchors = tf.constant(anchors, dtype='float', shape=[1, 1, 1, 9, 2])
    C = FLAGS.num_classes
    ignore_thresh = 0.5
    batch_size = FLAGS.batch_size

    cellbase_x = tf.to_float(tf.reshape(tf.tile(tf.range(52), [52]), (1, 52, 52, 1, 1)))
    cellbase_y = tf.transpose(cellbase_x, (0, 2, 1, 3, 4))
    cellbase_grid = tf.tile(tf.concat([cellbase_x, cellbase_y], -1), [batch_size, 1, 1, 3, 1])

    img_w = FLAGS.image_size
    img_h = FLAGS.image_size
    img_factor = tf.reshape(tf.cast([img_w, img_h], tf.float32), [1, 1, 1, 1, 2])

    loss = 0
    sum_loss_xy = 0
    sum_loss_wh = 0
    sum_loss_c = 0
    sum_loss_class = 0
    for i in range(3):
        # TODO:adjust the order of the anchor
        anchor = anchors[..., 3 * i:3 * (i + 1), :]
        object_mask = y_true[i][..., 4:5]

        grid_w = tf.shape(y_pred[i])[1]  # 13
        grid_h = tf.shape(y_pred[i])[2]  # 13
        grid_factor = tf.reshape(tf.cast([grid_w, grid_h], tf.float32), [1, 1, 1, 1, 2])

        net_out_reshape = tf.reshape(y_pred[i], [-1, grid_w, grid_h, 3, (4 + 1 + C)])
        adjusted_out_xy = (cellbase_grid[:, :grid_w, :grid_h, :, :] + tf.sigmoid(
            net_out_reshape[..., :2])) / grid_factor
        adjusted_out_wh = tf.exp(net_out_reshape[..., 2:4]) * anchor / img_factor
        adjusted_out_c = tf.expand_dims(tf.sigmoid(net_out_reshape[..., 4]), axis=-1)
        adjusted_out_class = tf.sigmoid(net_out_reshape[..., 5:])
        adjusted_net_out = tf.concat([adjusted_out_xy, adjusted_out_wh, adjusted_out_c, adjusted_out_class],
                                     axis=-1)
        pred_boxes = tf.expand_dims(adjusted_net_out[..., 0:4], 4)

        adjusted_true_xy = y_true[i][..., :2] * grid_factor - cellbase_grid[:, :grid_w, :grid_h, :, :]
        adjusted_true_wh = tf.log(y_true[i][..., 2:4] / anchor * img_factor + 1e-9)  # 1e-9 just avoid log(0) = -inf

        adjusted_true_c = y_true[i][..., 4:5]
        adjusted_true_class = y_true[i][..., 5:]

        # TODO i don't like for loop
        # origin_boxes = list()
        ignore_masks = list()
        for k in range(batch_size):
            origin_box = tf.boolean_mask(y_true[i][k, ..., :4], tf.cast(y_true[i][k, ..., 4], dtype=bool))
            origin_box = tf.tile(tf.reshape(origin_box, shape=[1, 1, 1, -1, 4]), [grid_w, grid_h, 3, 1, 1])
            iou_scores = iou(pred_boxes[k], origin_box)
            best_ious = tf.reduce_max(iou_scores, axis=-1)
            ignore_mask = tf.expand_dims(tf.to_float(best_ious < ignore_thresh), -1)
            ignore_masks.append(ignore_mask)
        ignore_masks = tf.stack(ignore_masks)
        # origin_boxes.append(origin_box)
        # # origin_boxes = tf.stack(origin_boxes)
        # iou_scores = iou(pred_boxes, origin_boxes)
        # best_ious = tf.reduce_max(iou_scores, axis=-1)
        # ignore_mask = tf.expand_dims(tf.to_float(best_ious < ignore_thresh), 4)
        xywh_scale = 2 - y_true[i][..., 2:3] * y_true[i][..., 3:4]

        loss_xy = tf.reduce_sum(
            object_mask * xywh_scale * tf.nn.sigmoid_cross_entropy_with_logits(logits=net_out_reshape[..., :2],
                                                                               labels=adjusted_true_xy)) / batch_size
        loss_wh = tf.reduce_sum(
            object_mask * xywh_scale * 0.5 * tf.square(net_out_reshape[..., 2:4] - adjusted_true_wh)) / batch_size
        loss_c = tf.reduce_sum(
            object_mask * tf.nn.sigmoid_cross_entropy_with_logits(logits=net_out_reshape[..., 4:5],
                                                                  labels=adjusted_true_c) + (
                    1 - object_mask) * tf.nn.sigmoid_cross_entropy_with_logits(logits=net_out_reshape[..., 4:5],
                                                                               labels=adjusted_true_c) * ignore_masks) / batch_size
        loss_class = tf.reduce_sum(
            object_mask * tf.nn.sigmoid_cross_entropy_with_logits(logits=net_out_reshape[..., 5:],
                                                                  labels=adjusted_true_class)) / batch_size

        sum_loss_xy += loss_xy
        sum_loss_wh += loss_wh
        sum_loss_c += loss_c
        sum_loss_class += loss_class
        loss += loss_xy + loss_wh + loss_c + loss_class

    tf.summary.scalar('loss', loss)
    tf.summary.scalar('loss_xy', sum_loss_xy)
    tf.summary.scalar('loss_wh', sum_loss_wh)
    tf.summary.scalar('loss_c', sum_loss_c)
    tf.summary.scalar('loss_class', sum_loss_class)
    # loss = tf.Print(loss, [sum_loss_xy, sum_loss_wh, sum_loss_c, sum_loss_class])
    return loss,sum_loss_xy,sum_loss_wh,sum_loss_c,sum_loss_class

In [15]:
def iou(pre_boxes, true_boxes):
    pred_xy = pre_boxes[..., :2]
    pred_wh = pre_boxes[..., 2:4]
    true_xy = true_boxes[..., :2]
    true_wh = true_boxes[..., 2:4]

    pred_wh_half = pred_wh / 2.
    pred_mins = pred_xy - pred_wh_half
    pred_maxes = pred_xy + pred_wh_half

    true_wh_half = true_wh / 2.
    true_mins = true_xy - true_wh_half
    true_maxes = true_xy + true_wh_half

    intersect_mins = tf.maximum(pred_mins, true_mins)
    intersect_maxes = tf.minimum(pred_maxes, true_maxes)

    intersect_wh = tf.maximum(intersect_maxes - intersect_mins, 0.)
    intersect_areas = intersect_wh[..., 0] * intersect_wh[..., 1]

    true_areas = true_wh[..., 0] * true_wh[..., 1]
    pred_areas = pred_wh[..., 0] * pred_wh[..., 1]

    union_areas = pred_areas + true_areas - intersect_areas
    iou_score = tf.truediv(intersect_areas, union_areas)

    return iou_score

In [16]:
def standardize_boxes(annotation_batch,default_padding = 15):
    temp_anno = []
    for i in range(len(annotation_batch)):
        temp = annotation_batch[i]
        for j in range(default_padding-annotation_batch[i].shape[0]):
            temp = np.vstack([temp,np.array([0,0,0,0,0])])
        temp_anno.append(temp.astype(np.int32))
    annotation_batch = temp_anno
    return np.array(annotation_batch)

In [17]:
def yolo_head_2(net_out, anchors, n_class, input_shape):
    boxes = list()
    box_scores = list()

    cellbase_x = tf.to_float(tf.reshape(tf.tile(tf.range(52), [52]), (1, 52, 52, 1, 1)))
    cellbase_y = tf.transpose(cellbase_x, (0, 2, 1, 3, 4))
    cellbase_grid = tf.tile(tf.concat([cellbase_x, cellbase_y], -1), [1, 1, 1, 3, 1])
    anchors = tf.constant(anchors, dtype='float', shape=[1, 1, 1, 9, 2])
    
    temp_box_confidence = []
    temp_box_class_probs = []
    temp_box_wh = []
    temp_box_yx = []
    for i in range(3):  # 52 26 13
        anchor = anchors[..., 3 * i:3 * (i + 1), :]
        # feats = model.output[i]
        feats = net_out[i]

        grid_w = tf.shape(feats)[1]  # 13
        grid_h = tf.shape(feats)[2]  # 13
        grid_factor = tf.reshape(tf.cast([grid_w, grid_h], tf.float32), [1, 1, 1, 1, 2])

        feats = tf.reshape(feats, [-1, grid_w, grid_h, 3, n_class + 5])

        # Adjust preditions to each spatial grid point and anchor size.
        box_xy = (tf.sigmoid(feats[..., :2]) + cellbase_grid[:, :grid_w, :grid_h, :, :]) / tf.cast(grid_factor[::-1],
                                                                                                   'float32')
        box_wh = tf.exp(feats[..., 2:4]) * anchor / tf.cast(input_shape[::-1], 'float32')
        box_confidence = tf.sigmoid(feats[..., 4:5])
        box_class_probs = tf.sigmoid(feats[..., 5:])

        box_yx = box_xy[..., ::-1]
        box_hw = box_wh[..., ::-1]
#         box_yx = (box_yx - offset) * scale
#         box_hw *= scale
        box_mins = box_yx - (box_hw / 2.)
        box_maxes = box_yx + (box_hw / 2.)
        _boxes = tf.concat([
            box_mins[..., 0:1],  # y_min
            box_mins[..., 1:2],  # x_min
            box_maxes[..., 0:1],  # y_max
            box_maxes[..., 1:2]  # x_max
        ], axis=-1)

        # Scale boxes back to (416,416) image shape.
        _boxes *= tf.concat([tf.cast((416,416), 'float32'), tf.cast((416,416), 'float32')], axis=-1)
        _boxes = tf.reshape(_boxes, [-1, 4])

        _box_scores = box_confidence * box_class_probs
        _box_scores = tf.reshape(_box_scores, [-1, n_class])
        boxes.append(_boxes)
        box_scores.append(_box_scores)
        
    boxes = tf.concat(boxes, axis=0)
    box_scores = tf.concat(box_scores, axis=0)

    mask = box_scores >= 0.5
    max_num_boxes = tf.constant(20, dtype='int32')

    boxes_ = []
    scores_ = []
    classes_ = []
    for c in range(n_class):
        class_boxes = tf.boolean_mask(boxes, mask[:, c])
        class_box_scores = tf.boolean_mask(box_scores[:, c], mask[:, c])
        nms_index = tf.image.non_max_suppression(
            class_boxes, class_box_scores, max_num_boxes, iou_threshold=0.5)
        class_boxes = tf.gather(class_boxes, nms_index)
        class_box_scores = tf.gather(class_box_scores, nms_index)
        classes = tf.ones_like(class_box_scores, 'int32') * c
        boxes_.append(class_boxes)
        scores_.append(class_box_scores)
        classes_.append(classes)
    boxes_ = tf.concat(boxes_, axis=0,name='boxes')
    scores_ = tf.concat(scores_, axis=0,name ='scores')
    classes_ = tf.concat(classes_, axis=0,name='classes')
    return boxes_,scores_,classes_

In [18]:
anchors = []
with open('./data/yolo_anchors.txt','r') as f:
    for line in f.readlines():
        anchors.append(line.strip('\n'))
temp = anchors[0].split(', ')
temp_list = []
for i in temp:
    temp_list.append(i.split(','))
temp_list = np.array(temp_list)
anchors = temp_list.astype(np.float32)
num_anchors = len(anchors)//3

In [19]:
inputs = tf.placeholder(tf.float32, [None, 416, 416, 3],name='inputs')
y_true_1 = tf.placeholder(tf.float32, [None, 13, 13, 3, 42])
y_true_2 = tf.placeholder(tf.float32, [None, 26, 26, 3, 42])
y_true_3 = tf.placeholder(tf.float32, [None, 52, 52, 3, 42])
is_training = tf.placeholder(tf.bool,name='is_training')
layer = inputs 

#bottle neck
X,scale1,scale2,scale3 = bottle_neck(layer,is_training)
# print(X.shape)
#scale1 13*13
X,scale1 = scale(X,scale1,512,num_anchors,FLAGS.num_classes,is_training)

#scale2 26*26
X,scale2 = scale(X,scale2,256,num_anchors,FLAGS.num_classes,is_training)

#scale 52*52
X,scale3 = scale(X,scale3,128,num_anchors,FLAGS.num_classes,is_training)

scale1 = tf.reshape(scale1,(-1,13,13,num_anchors,FLAGS.num_classes+5))
scale2 = tf.reshape(scale2,(-1,26,26,num_anchors,FLAGS.num_classes+5))
scale3 = tf.reshape(scale3,(-1,52,52,num_anchors,FLAGS.num_classes+5))
y_pred = [scale3,scale2,scale1]
boxes_,scores_,classes_ = yolo_head_2(y_pred, anchors, FLAGS.num_classes, (FLAGS.image_size,FLAGS.image_size))

In [20]:
learning_rate = 0.0001
# tf.summary.scalar('loss',total_losses)

loss,loss_xy,loss_wh,loss_c,loss_class = yolo3_loss(y_pred, [y_true_3,y_true_2,y_true_1],anchors)
update_opts = tf.get_collection(tf.GraphKeys.UPDATE_OPS)
with tf.control_dependencies([tf.group(*update_opts)]):
    train_opt = tf.train.AdamOptimizer(learning_rate).minimize(loss)
with tf.Session() as sess:
    train_writer = tf.summary.FileWriter(FLAGS.log_dir,sess.graph)
    saver = tf.train.Saver(max_to_keep=5)
    img_path, annotation = get_path_and_annotation('./data/train_ocr.txt')
    train_feeder = read_data(img_path,annotation,FLAGS.batch_size,False)
    sess.run(tf.global_variables_initializer())
    ckpt = tf.train.latest_checkpoint(FLAGS.checkpoint_dir)
    if ckpt:
        saver.restore(sess,ckpt)
        print('Restore from the checkpoint {0}'.format(ckpt))
    else:
        print('Train yolo from start')
    for i in range(50000):
        image_batch, annotation_batch = next(train_feeder)
        image_batch, annotation_batch = resize_images_boxes(image_batch,annotation_batch,15)
        y_true = preprocess_true_boxes(annotation_batch, (FLAGS.image_size,FLAGS.image_size), anchors, FLAGS.num_classes)
        [_,total_loss,current_lossxy,current_losswh,current_lossc,current_loss_class,temp_pred] = sess.run([train_opt,loss,loss_xy,loss_wh,loss_c,loss_class,y_pred],feed_dict={inputs:image_batch,y_true_1:y_true[0],y_true_2:y_true[1],y_true_3:y_true[2],is_training: True})
        if(i%500 == 0):
            saver.save(sess,os.path.join(FLAGS.checkpoint_dir,'OCR-'),global_step=i)
            print('Model saved!!')
            
            #######################################################################
            constant_graph = convert_variables_to_constants(sess, sess.graph_def, ['boxes','scores','classes'])
            with tf.gfile.FastGFile('./model.pb', mode='wb') as f:
                f.write(constant_graph.SerializeToString())
            ######################################################################
            
            
            
        print('Batch: '+str(i)+'   Current total loss: '+str(total_loss)+'  loss_xy: '+str(current_lossxy)+'  loss_wh: '+str(current_losswh)+'  loss_c: '+str(current_lossc)+' loss_class: '+str(current_loss_class))

INFO:tensorflow:Restoring parameters from ./checkpoint/OCR--0
Restore from the checkpoint ./checkpoint/OCR--0
Model saved!!
INFO:tensorflow:Froze 336 variables.
INFO:tensorflow:Converted 336 variables to const ops.
Batch: 0   Current total loss: 8189.1284  loss_xy: 47.147614  loss_wh: 65.314224  loss_c: 7518.6675 loss_class: 557.9988
Batch: 1   Current total loss: 7720.094  loss_xy: 38.70432  loss_wh: 45.497765  loss_c: 7217.3823 loss_class: 418.5099
Batch: 2   Current total loss: 7207.3354  loss_xy: 33.93354  loss_wh: 31.020187  loss_c: 6810.721 loss_class: 331.66043
Batch: 3   Current total loss: 6779.3066  loss_xy: 31.543562  loss_wh: 28.171932  loss_c: 6454.615 loss_class: 264.97598
Batch: 4   Current total loss: 6415.366  loss_xy: 31.00483  loss_wh: 21.22536  loss_c: 6135.6304 loss_class: 227.50584
Batch: 5   Current total loss: 6067.1494  loss_xy: 30.020847  loss_wh: 16.928915  loss_c: 5823.7495 loss_class: 196.45041
Batch: 6   Current total loss: 5734.487  loss_xy: 28.648739  lo

Batch: 66   Current total loss: 1357.2019  loss_xy: 25.304747  loss_wh: 1.3189992  loss_c: 1268.2802 loss_class: 62.297924
Batch: 67   Current total loss: 1337.6533  loss_xy: 25.01905  loss_wh: 0.9205094  loss_c: 1255.3538 loss_class: 56.359993
Batch: 68   Current total loss: 1329.1345  loss_xy: 25.542889  loss_wh: 1.037798  loss_c: 1244.0623 loss_class: 58.49152
Batch: 69   Current total loss: 1315.481  loss_xy: 24.97742  loss_wh: 0.85220736  loss_c: 1232.6755 loss_class: 56.97579
Batch: 70   Current total loss: 1303.0295  loss_xy: 24.602905  loss_wh: 0.84888065  loss_c: 1221.58 loss_class: 55.997772
Batch: 71   Current total loss: 1292.3469  loss_xy: 24.59277  loss_wh: 0.9490636  loss_c: 1210.8402 loss_class: 55.964855
Batch: 72   Current total loss: 1281.9648  loss_xy: 25.057995  loss_wh: 0.79459226  loss_c: 1200.5526 loss_class: 55.55973
Batch: 73   Current total loss: 1271.8973  loss_xy: 24.783485  loss_wh: 1.0921329  loss_c: 1189.796 loss_class: 56.225746
Batch: 74   Current tota

Batch: 133   Current total loss: 860.3353  loss_xy: 23.401052  loss_wh: 0.6742598  loss_c: 800.90607 loss_class: 35.353947
Batch: 134   Current total loss: 856.69525  loss_xy: 23.217  loss_wh: 0.78464866  loss_c: 796.3051 loss_class: 36.388504
Batch: 135   Current total loss: 853.26953  loss_xy: 23.19187  loss_wh: 0.6532726  loss_c: 792.67316 loss_class: 36.75122
Batch: 136   Current total loss: 845.9668  loss_xy: 23.691994  loss_wh: 0.6442827  loss_c: 787.6133 loss_class: 34.01718
Batch: 137   Current total loss: 842.401  loss_xy: 22.916742  loss_wh: 0.5989148  loss_c: 783.5575 loss_class: 35.327835
Batch: 138   Current total loss: 838.68005  loss_xy: 23.431469  loss_wh: 0.59709275  loss_c: 779.04785 loss_class: 35.60371
Batch: 139   Current total loss: 837.26746  loss_xy: 22.863129  loss_wh: 0.8305076  loss_c: 775.5664 loss_class: 38.00738
Batch: 140   Current total loss: 830.96716  loss_xy: 23.215395  loss_wh: 0.7273468  loss_c: 771.3039 loss_class: 35.720512
Batch: 141   Current to

Batch: 200   Current total loss: 628.5605  loss_xy: 22.956966  loss_wh: 0.48164868  loss_c: 576.28375 loss_class: 28.838148
Batch: 201   Current total loss: 622.0004  loss_xy: 21.830933  loss_wh: 0.51983  loss_c: 573.7285 loss_class: 25.921152
Batch: 202   Current total loss: 621.75586  loss_xy: 22.486624  loss_wh: 0.6100246  loss_c: 571.0659 loss_class: 27.593246
Batch: 203   Current total loss: 621.6233  loss_xy: 22.290236  loss_wh: 0.5511852  loss_c: 568.57465 loss_class: 30.207205
Batch: 204   Current total loss: 616.2192  loss_xy: 22.660437  loss_wh: 0.61444837  loss_c: 566.25085 loss_class: 26.693396
Batch: 205   Current total loss: 613.6076  loss_xy: 22.59988  loss_wh: 0.64406914  loss_c: 563.1491 loss_class: 27.214537
Batch: 206   Current total loss: 610.6423  loss_xy: 22.244652  loss_wh: 0.5814164  loss_c: 560.9402 loss_class: 26.876062
Batch: 207   Current total loss: 608.1468  loss_xy: 22.57619  loss_wh: 0.5549914  loss_c: 559.149 loss_class: 25.866644
Batch: 208   Current t

Batch: 267   Current total loss: 480.36328  loss_xy: 22.77949  loss_wh: 0.47408217  loss_c: 435.95303 loss_class: 21.156677
Batch: 268   Current total loss: 478.77936  loss_xy: 22.40446  loss_wh: 0.5141405  loss_c: 434.6783 loss_class: 21.182447
Batch: 269   Current total loss: 477.5535  loss_xy: 22.239967  loss_wh: 0.5595999  loss_c: 432.87537 loss_class: 21.878584
Batch: 270   Current total loss: 479.73608  loss_xy: 22.253942  loss_wh: 0.63677645  loss_c: 431.5816 loss_class: 25.263733
Batch: 271   Current total loss: 473.64932  loss_xy: 22.278255  loss_wh: 0.5212301  loss_c: 429.74597 loss_class: 21.103844
Batch: 272   Current total loss: 477.89392  loss_xy: 22.04485  loss_wh: 0.790743  loss_c: 427.97888 loss_class: 27.079464
Batch: 273   Current total loss: 469.62  loss_xy: 22.176468  loss_wh: 0.6124144  loss_c: 426.40842 loss_class: 20.42269
Batch: 274   Current total loss: 469.77087  loss_xy: 22.396673  loss_wh: 0.5518165  loss_c: 424.6741 loss_class: 22.148289
Batch: 275   Curre

...

Batch: 49738   Current total loss: 20.998293  loss_xy: 20.922535  loss_wh: 0.0723233  loss_c: 0.00036467626 loss_class: 0.003071387
Batch: 49739   Current total loss: 19.929062  loss_xy: 19.88079  loss_wh: 0.040964928  loss_c: 0.0005221493 loss_class: 0.0067852614
Batch: 49740   Current total loss: 20.006702  loss_xy: 19.9709  loss_wh: 0.03448804  loss_c: 0.00035431108 loss_class: 0.0009592336
Batch: 49741   Current total loss: 21.05143  loss_xy: 21.012506  loss_wh: 0.037541375  loss_c: 0.00052867533 loss_class: 0.00085487927
Batch: 49742   Current total loss: 20.117836  loss_xy: 20.066732  loss_wh: 0.04836217  loss_c: 0.00096020935 loss_class: 0.0017807996
Batch: 49743   Current total loss: 20.25816  loss_xy: 20.22077  loss_wh: 0.03502677  loss_c: 0.0012077311 loss_class: 0.0011557041
Batch: 49744   Current total loss: 20.28438  loss_xy: 20.252378  loss_wh: 0.030243857  loss_c: 0.0005440599 loss_class: 0.0012146013
Batch: 49745   Current total loss: 20.194578  loss_xy: 20.162907  loss

Batch: 49800   Current total loss: 20.475222  loss_xy: 20.454319  loss_wh: 0.017137824  loss_c: 0.0021802352 loss_class: 0.0015848014
Batch: 49801   Current total loss: 20.05869  loss_xy: 20.02427  loss_wh: 0.026210517  loss_c: 0.006911272 loss_class: 0.0012980346
Batch: 49802   Current total loss: 20.886526  loss_xy: 20.69843  loss_wh: 0.020233355  loss_c: 0.16631171 loss_class: 0.0015520668
Batch: 49803   Current total loss: 20.450718  loss_xy: 20.426472  loss_wh: 0.016886076  loss_c: 0.0064251227 loss_class: 0.00093455863
Batch: 49804   Current total loss: 20.344831  loss_xy: 20.32318  loss_wh: 0.017219942  loss_c: 0.0030941323 loss_class: 0.0013390935
Batch: 49805   Current total loss: 21.033487  loss_xy: 20.995502  loss_wh: 0.025720984  loss_c: 0.009208702 loss_class: 0.0030562363
Batch: 49806   Current total loss: 19.787998  loss_xy: 19.767826  loss_wh: 0.015029468  loss_c: 0.0039167255 loss_class: 0.0012268039
Batch: 49807   Current total loss: 20.612312  loss_xy: 20.597048  los

Batch: 49862   Current total loss: 21.533016  loss_xy: 20.914404  loss_wh: 0.055703945  loss_c: 0.0005322079 loss_class: 0.56237596
Batch: 49863   Current total loss: 20.870838  loss_xy: 20.827103  loss_wh: 0.040692575  loss_c: 0.0009199376 loss_class: 0.0021235761
Batch: 49864   Current total loss: 20.173239  loss_xy: 20.107878  loss_wh: 0.03809331  loss_c: 0.0031940127 loss_class: 0.02407201
Batch: 49865   Current total loss: 20.63246  loss_xy: 20.602348  loss_wh: 0.02763632  loss_c: 0.0010514205 loss_class: 0.0014238665
Batch: 49866   Current total loss: 20.480879  loss_xy: 20.423864  loss_wh: 0.0474237  loss_c: 0.0052009975 loss_class: 0.0043894993
Batch: 49867   Current total loss: 20.260216  loss_xy: 20.20831  loss_wh: 0.04865875  loss_c: 0.0010535864 loss_class: 0.0021958032
Batch: 49868   Current total loss: 20.845186  loss_xy: 20.792116  loss_wh: 0.049026288  loss_c: 0.0016569638 loss_class: 0.002386167
Batch: 49869   Current total loss: 22.065092  loss_xy: 21.532787  loss_wh:

Batch: 49924   Current total loss: 20.629932  loss_xy: 20.606678  loss_wh: 0.018073896  loss_c: 0.0013402313 loss_class: 0.003838844
Batch: 49925   Current total loss: 21.229109  loss_xy: 21.142633  loss_wh: 0.08436768  loss_c: 0.000528365 loss_class: 0.0015792826
Batch: 49926   Current total loss: 20.033564  loss_xy: 19.955318  loss_wh: 0.039233286  loss_c: 0.020415623 loss_class: 0.018594984
Batch: 49927   Current total loss: 20.334116  loss_xy: 20.313557  loss_wh: 0.019525673  loss_c: 0.00041898194 loss_class: 0.0006144981
Batch: 49928   Current total loss: 20.19113  loss_xy: 20.17403  loss_wh: 0.015853545  loss_c: 0.00044690163 loss_class: 0.0007982263
Batch: 49929   Current total loss: 20.606783  loss_xy: 20.58891  loss_wh: 0.016734708  loss_c: 0.0003452212 loss_class: 0.00079333206
Batch: 49930   Current total loss: 20.367342  loss_xy: 20.321898  loss_wh: 0.043617457  loss_c: 0.00052896206 loss_class: 0.0012996425
Batch: 49931   Current total loss: 20.199974  loss_xy: 20.174345  

Batch: 49985   Current total loss: 20.735605  loss_xy: 20.727901  loss_wh: 0.0070417617  loss_c: 0.00024334817 loss_class: 0.00041718065
Batch: 49986   Current total loss: 20.25417  loss_xy: 20.247324  loss_wh: 0.006063289  loss_c: 0.00028403135 loss_class: 0.0004969475
Batch: 49987   Current total loss: 20.248106  loss_xy: 20.239824  loss_wh: 0.007066598  loss_c: 0.00026351455 loss_class: 0.0009525478
Batch: 49988   Current total loss: 20.199293  loss_xy: 20.188093  loss_wh: 0.010265258  loss_c: 0.00041137487 loss_class: 0.00052179757
Batch: 49989   Current total loss: 20.056974  loss_xy: 20.045456  loss_wh: 0.009317638  loss_c: 0.0013190487 loss_class: 0.0008810466
Batch: 49990   Current total loss: 20.04395  loss_xy: 20.035263  loss_wh: 0.007948329  loss_c: 0.00033409867 loss_class: 0.00040484843
Batch: 49991   Current total loss: 20.149277  loss_xy: 20.139883  loss_wh: 0.00873034  loss_c: 0.00018410335 loss_class: 0.00047864177
Batch: 49992   Current total loss: 21.24943  loss_xy: 